In [1]:
# Import dependencies
import pandas as pd
import numpy as np
import json 
import requests
import timeit
from datetime import datetime

In [2]:
file_path="Resources/Electric_Vehicle_Charging_Stations_in_New_York.csv"
Charger_df=pd.read_csv(file_path)
Charger_df

Fuel Type Code                Station Name                Street Address  \
0              ELEC  Town of Penfield - Library                 1985 Baird Rd   
1              ELEC          Village of Webster           28 West Main Street   
2              ELEC   HOTSARA CHARGER STATION 1                   100 Main St   
3              ELEC            Houghton College                    9736 Rt 19   
4              ELEC    NYC FLEET DPRMBLOT8_1_L3     920 Father Capodanno Blvd   
...             ...                         ...                           ...   
3079           ELEC       W DELAVAN DELAVAN (1)             722 W Delavan Ave   
3080           ELEC       HAMPTON INN STATION 1                1120 South Ave   
3081           ELEC    SRYMCASSB BATTENKILL 1.1               15 Van Ness Ave   
3082           ELEC  PAUL MILLER VW VW_408107_A           5865 Rome-Taberg Rd   
3083           ELEC        GENESEO E PARK RIGHT  4319 Genesee Valley Plaza Rd   

     Intersection Directions           City State    ZIP  Plus4 Station Phone  \
0                        NaN       Penfield    NY  14526    NaN  585-340-8720   
1                        NaN        Webster    NY  14580    NaN  866-816-7584   
2                        NaN   Saranac Lake    NY  12983    NaN  888-758-4389   
3                        NaN       Houghton    NY  14744    NaN  866-816-7584   
4                        NaN  Midland Beach    NY  10305    NaN  888-758-4389   
...                      ...            ...   ...    ...    ...           ...   
3079                     NaN        Buffalo    NY  14222    NaN  888-758-4389   
3080                     NaN  Staten Island    NY  10314    NaN  888-758-4389   
3081                     NaN      Greenwich    NY  12834    NaN  888-758-4389   
3082                     NaN           Rome    NY  13440    NaN  888-758-4389   
3083                     NaN        Geneseo    NY  14454    NaN  888-758-4389   

     Status Code  ...   Latitude  Longitude Date Last Confirmed      ID  \
0              E  ...  43.137476 -77.465214          06/07/2021   49941   
1              E  ...  43.211386 -77.431663          11/10/2022  116756   
2              E  ...  44.326862 -74.130150          11/10/2022  149787   
3              E  ...  42.423869 -78.154428          11/10/2022  157942   
4              E  ...  40.572636 -74.086140          11/10/2022  182295   
...          ...  ...        ...        ...                 ...     ...   
3079           E  ...  42.922743 -78.873098          11/10/2022  154370   
3080           E  ...  40.612696 -74.179012          11/10/2022  168146   
3081           E  ...  43.093964 -73.506775          11/10/2022  183460   
3082           E  ...  43.233239 -75.497597          11/10/2022  152393   
3083           E  ...  42.798031 -77.783211          11/10/2022  224227   

               Updated At  Owner Type Code  Federal Agency ID  \
0     2022-02-10 19:42:29               LG                NaN   
1     2022-11-10 02:00:34              NaN                NaN   
2     2022-11-10 00:57:46              NaN                NaN   
3     2022-11-10 02:00:45              NaN                NaN   
4     2022-11-10 01:05:12              NaN                NaN   
...                   ...              ...                ...   
3079  2022-11-10 01:01:48              NaN                NaN   
3080  2022-11-10 01:05:20              NaN                NaN   
3081  2022-11-10 01:06:06              NaN                NaN   
3082  2022-11-10 00:42:37              NaN                NaN   
3083  2022-11-10 01:15:40              NaN                NaN   

     Federal Agency Name   Open Date  EV Connector Types  
0                    NaN  04/01/2012               J1772  
1                    NaN  08/31/2018               J1772  
2                    NaN  12/07/2019               J1772  
3                    NaN  05/15/2020               J1772  
4                    NaN  01/27/2021  CHADEMO J1772COMBO  
...                  ..

In [3]:
Charger_df.columns


Index(['Fuel Type Code', 'Station Name', 'Street Address',
       'Intersection Directions', 'City', 'State', 'ZIP', 'Plus4',
       'Station Phone', 'Status Code', 'Expected Date',
       'Groups With Access Code', 'Access Days Time', 'Cards Accepted',
       'EV Level1 EVSE Num', 'EV Level2 EVSE Num', 'EV DC Fast Count',
       'EV Other Info', 'EV Network', 'EV Network Web', 'Geocode Status',
       'Latitude', 'Longitude', 'Date Last Confirmed', 'ID', 'Updated At',
       'Owner Type Code', 'Federal Agency ID', 'Federal Agency Name',
       'Open Date', 'EV Connector Types'],
      dtype='object')

In [4]:
Charger_df = Charger_df [['ID','Station Name', 'City','State','ZIP']]
Charger_df

ID                Station Name           City State    ZIP
0      49941  Town of Penfield - Library       Penfield    NY  14526
1     116756          Village of Webster        Webster    NY  14580
2     149787   HOTSARA CHARGER STATION 1   Saranac Lake    NY  12983
3     157942            Houghton College       Houghton    NY  14744
4     182295    NYC FLEET DPRMBLOT8_1_L3  Midland Beach    NY  10305
...      ...                         ...            ...   ...    ...
3079  154370       W DELAVAN DELAVAN (1)        Buffalo    NY  14222
3080  168146       HAMPTON INN STATION 1  Staten Island    NY  10314
3081  183460    SRYMCASSB BATTENKILL 1.1      Greenwich    NY  12834
3082  152393  PAUL MILLER VW VW_408107_A           Rome    NY  13440
3083  224227        GENESEO E PARK RIGHT        Geneseo    NY  14454

[3084 rows x 5 columns]

In [5]:
Charger_df['City'].nunique()

570

In [6]:
from uszipcode import SearchEngine

C:\Users\simro\anaconda3\envs\mlenv\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [7]:
#Creating a dictionary that shows which county each zipcode is in
zipcodes_to_search = list(Charger_df['ZIP'].unique())
search = SearchEngine()
zip_map = {}

# excluding the zipcode not corresponded to any county
for zipcode in zipcodes_to_search:
    if zipcode == 12081:
        pass
    elif zipcode == 12217:
        pass
    else:
        zip_info = search.by_zipcode(zipcode).county
        zip_map[zipcode] = zip_info

zip_map

{14526: 'Monroe County',
 14580: 'Monroe County',
 12983: 'Franklin County',
 14744: 'Allegany County',
 10305: 'Richmond County',
 14227: 'Erie County',
 11220: 'Kings County',
 13090: 'Onondaga County',
 10954: 'Rockland County',
 14853: 'Tompkins County',
 11040: 'Nassau County',
 12205: 'Albany County',
 11976: 'Suffolk County',
 12590: 'Dutchess County',
 11212: 'Kings County',
 12534: 'Columbia County',
 14204: 'Erie County',
 10901: 'Rockland County',
 12180: 'Rensselaer County',
 10065: 'New York County',
 13027: 'Onondaga County',
 14621: 'Monroe County',
 11954: 'Suffolk County',
 11710: 'Nassau County',
 12110: 'Albany County',
 11901: 'Suffolk County',
 12020: 'Saratoga County',
 12477: 'Ulster County',
 13441: 'Oneida County',
 12144: 'Rensselaer County',
 14223: 'Erie County',
 14850: 'Tompkins County',
 14616: 'Monroe County',
 12054: 'Albany County',
 12866: 'Saratoga County',
 14731: 'Cattaraugus County',
 10022: 'New York County',
 14072: 'Erie County',
 12065: 'Sarat

In [8]:
#mapping county information for each charger based on zipcode
Charger_df['County'] = Charger_df['ZIP'].map(zip_map) 
Charger_df.head()

C:\Users\simro\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


ID                Station Name           City State    ZIP  \
0   49941  Town of Penfield - Library       Penfield    NY  14526   
1  116756          Village of Webster        Webster    NY  14580   
2  149787   HOTSARA CHARGER STATION 1   Saranac Lake    NY  12983   
3  157942            Houghton College       Houghton    NY  14744   
4  182295    NYC FLEET DPRMBLOT8_1_L3  Midland Beach    NY  10305   

            County  
0    Monroe County  
1    Monroe County  
2  Franklin County  
3  Allegany County  
4  Richmond County

In [9]:
import pgeocode
zipcodes_to_search = list(Charger_df['ZIP'].unique())

nomi = pgeocode.Nominatim('us')


latitude_map = {}

for zipcode in zipcodes_to_search:
    if zipcode == 12081:
        pass
    elif zipcode == 12217:
        pass
    else:
        latitude_info = nomi.query_postal_code(str(zipcode)).latitude
        latitude_map[zipcode] = latitude_info

latitude_map

Charger_df['latitude_station'] = Charger_df['ZIP'].map(latitude_map) 
Charger_df

C:\Users\simro\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


ID                Station Name           City State    ZIP  \
0      49941  Town of Penfield - Library       Penfield    NY  14526   
1     116756          Village of Webster        Webster    NY  14580   
2     149787   HOTSARA CHARGER STATION 1   Saranac Lake    NY  12983   
3     157942            Houghton College       Houghton    NY  14744   
4     182295    NYC FLEET DPRMBLOT8_1_L3  Midland Beach    NY  10305   
...      ...                         ...            ...   ...    ...   
3079  154370       W DELAVAN DELAVAN (1)        Buffalo    NY  14222   
3080  168146       HAMPTON INN STATION 1  Staten Island    NY  10314   
3081  183460    SRYMCASSB BATTENKILL 1.1      Greenwich    NY  12834   
3082  152393  PAUL MILLER VW VW_408107_A           Rome    NY  13440   
3083  224227        GENESEO E PARK RIGHT        Geneseo    NY  14454   

                 County  latitude_station  
0         Monroe County           43.1396  
1         Monroe County           43.2196  
2       Franklin County           44.3243  
3       Allegany County           42.4228  
4       Richmond County           40.5973  
...                 ...               ...  
3079        Erie County           42.9164  
3080    Richmond County           40.6039  
3081  Washington County           43.0947  
3082      Oneida County           43.2193  
3083  Livingston County           42.7938  

[3084 rows x 7 columns]

In [28]:
Charger_df.State.value_counts()

NY    3080
Name: State, dtype: int64

In [10]:
zipcodes_to_search = list(Charger_df['ZIP'].unique())

nomi = pgeocode.Nominatim('us')

longitude_map = {}

for zipcode in zipcodes_to_search:
    if zipcode == 12081:
        pass
    elif zipcode == 12217:
        pass
    else:
        longitude_info = nomi.query_postal_code(str(zipcode)).longitude
        longitude_map[zipcode] = longitude_info

longitude_map

Charger_df['longitude_station'] = Charger_df['ZIP'].map(longitude_map) 
Charger_df

C:\Users\simro\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


ID                Station Name           City State    ZIP  \
0      49941  Town of Penfield - Library       Penfield    NY  14526   
1     116756          Village of Webster        Webster    NY  14580   
2     149787   HOTSARA CHARGER STATION 1   Saranac Lake    NY  12983   
3     157942            Houghton College       Houghton    NY  14744   
4     182295    NYC FLEET DPRMBLOT8_1_L3  Midland Beach    NY  10305   
...      ...                         ...            ...   ...    ...   
3079  154370       W DELAVAN DELAVAN (1)        Buffalo    NY  14222   
3080  168146       HAMPTON INN STATION 1  Staten Island    NY  10314   
3081  183460    SRYMCASSB BATTENKILL 1.1      Greenwich    NY  12834   
3082  152393  PAUL MILLER VW VW_408107_A           Rome    NY  13440   
3083  224227        GENESEO E PARK RIGHT        Geneseo    NY  14454   

                 County  latitude_station  longitude_station  
0         Monroe County           43.1396           -77.4560  
1         Monroe County           43.2196           -77.4616  
2       Franklin County           44.3243           -74.1330  
3       Allegany County           42.4228           -78.2063  
4       Richmond County           40.5973           -74.0768  
...                 ...               ...                ...  
3079        Erie County           42.9164           -78.8763  
3080    Richmond County           40.6039           -74.1472  
3081  Washington County           43.0947           -73.5030  
3082      Oneida County           43.2193           -75.4498  
3083  Livingston County           42.7938           -77.7996  

[3084 rows x 8 columns]

In [11]:
#making County 's name compatible with the original dataset
# removing "County" after eanch county's name
Charger_df['County'] = Charger_df['County'].str[:-7]
Charger_df

C:\Users\simro\anaconda3\envs\mlenv\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


ID                Station Name           City State    ZIP  \
0      49941  Town of Penfield - Library       Penfield    NY  14526   
1     116756          Village of Webster        Webster    NY  14580   
2     149787   HOTSARA CHARGER STATION 1   Saranac Lake    NY  12983   
3     157942            Houghton College       Houghton    NY  14744   
4     182295    NYC FLEET DPRMBLOT8_1_L3  Midland Beach    NY  10305   
...      ...                         ...            ...   ...    ...   
3079  154370       W DELAVAN DELAVAN (1)        Buffalo    NY  14222   
3080  168146       HAMPTON INN STATION 1  Staten Island    NY  10314   
3081  183460    SRYMCASSB BATTENKILL 1.1      Greenwich    NY  12834   
3082  152393  PAUL MILLER VW VW_408107_A           Rome    NY  13440   
3083  224227        GENESEO E PARK RIGHT        Geneseo    NY  14454   

          County  latitude_station  longitude_station  
0         Monroe           43.1396           -77.4560  
1         Monroe           43.2196           -77.4616  
2       Franklin           44.3243           -74.1330  
3       Allegany           42.4228           -78.2063  
4       Richmond           40.5973           -74.0768  
...          ...               ...                ...  
3079        Erie           42.9164           -78.8763  
3080    Richmond           40.6039           -74.1472  
3081  Washington           43.0947           -73.5030  
3082      Oneida           43.2193           -75.4498  
3083  Livingston           42.7938           -77.7996  

[3084 rows x 8 columns]

In [12]:
# dropping NAAN values for longitude and latitude
Charger_df=Charger_df.dropna(subset=['longitude_station'])

Charger_df=Charger_df.dropna(subset=['latitude_station'])


In [13]:
Charger_df.dropna()

ID                Station Name           City State    ZIP  \
0      49941  Town of Penfield - Library       Penfield    NY  14526   
1     116756          Village of Webster        Webster    NY  14580   
2     149787   HOTSARA CHARGER STATION 1   Saranac Lake    NY  12983   
3     157942            Houghton College       Houghton    NY  14744   
4     182295    NYC FLEET DPRMBLOT8_1_L3  Midland Beach    NY  10305   
...      ...                         ...            ...   ...    ...   
3079  154370       W DELAVAN DELAVAN (1)        Buffalo    NY  14222   
3080  168146       HAMPTON INN STATION 1  Staten Island    NY  10314   
3081  183460    SRYMCASSB BATTENKILL 1.1      Greenwich    NY  12834   
3082  152393  PAUL MILLER VW VW_408107_A           Rome    NY  13440   
3083  224227        GENESEO E PARK RIGHT        Geneseo    NY  14454   

          County  latitude_station  longitude_station  
0         Monroe           43.1396           -77.4560  
1         Monroe           43.2196           -77.4616  
2       Franklin           44.3243           -74.1330  
3       Allegany           42.4228           -78.2063  
4       Richmond           40.5973           -74.0768  
...          ...               ...                ...  
3079        Erie           42.9164           -78.8763  
3080    Richmond           40.6039           -74.1472  
3081  Washington           43.0947           -73.5030  
3082      Oneida           43.2193           -75.4498  
3083  Livingston           42.7938           -77.7996  

[3080 rows x 8 columns]

In [14]:
# Exporting the DataFrame as WeatherPy_Database.csv into the Weather_Database folder
# defining the path
# Saving  clean data to CSV
Charger_df.to_csv('Resources/Demographic_Database_EV_Stations.csv')

In [15]:
lats = list(Charger_df['latitude_station'])
lngs = list(Charger_df['longitude_station'])

# pack the random coordinates into a zip
coordinates_list = zip(lats,lngs)

coordinates_list

In [16]:
coordinates= list(coordinates_list)
print(coordinates)

[(43.1396, -77.456), (43.2196, -77.4616), (44.3243, -74.133), (42.4228, -78.2063), (40.5973, -74.0768), (42.8853, -78.7462), (40.6412, -74.0133), (43.1528, -76.2235), (41.0977, -74.0109), (42.4474, -76.4837), (40.7294, -73.6828), (42.7198, -73.8207), (40.9209, -72.3491), (41.595, -73.8876), (40.6625, -73.9145), (42.247, -73.7552), (42.884, -78.8597), (41.1177, -74.1241), (42.7287, -73.6683), (40.7651, -73.9638), (43.162, -76.3237), (43.1834, -77.6043), (41.0459, -71.944), (42.247, -73.7552), (40.6729, -73.5365), (42.7462, -73.763), (40.9262, -72.652), (43.005, -73.8486), (42.0738, -73.9797), (43.2264, -75.4083), (42.6359, -73.7219), (42.9731, -78.845), (44.3243, -74.133), (42.4406, -76.4966), (43.2346, -77.6577), (42.6158, -73.8373), (42.4228, -78.2063), (43.0708, -73.7408), (42.2959, -78.6606), (43.0708, -73.7408), (40.7571, -73.9657), (43.0183, -78.9591), (42.8499, -73.7851), (40.9271, -73.0127), (42.7005, -74.9243), (41.7464, -74.1092), (40.7444, -73.0542), (42.7003, -73.8575), (40.

In [17]:
locations = Charger_df[['latitude_station', 'longitude_station']]
locationlist = locations.values.tolist()
locationlist= [[float(lat),float(lon)] for [lat,lon] in locationlist]

In [18]:
#let's change the look of the point icon
import folium
import pgeocode
from folium.plugins import MarkerCluster
map2 = folium.Map(location=[40.71427, -74.00597], tiles='Stamen Terrain', zoom_start=11)

marker_cluster = MarkerCluster().add_to(map2)

for point in range(0, len(locationlist)):
    try:
        folium.Marker(locationlist[point], popup=Charger_df['Station Name'][point], icon=folium.Icon(color='green', icon_color='white', icon='bolt', angle=0, prefix='fa')).add_to(marker_cluster)
    except KeyError:
        print('Can not find "something"')
map2

Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"


In [19]:
map2.save('New_York_state_EV_station map.html')

In [20]:
Charger_df.County.unique()

array(['Monroe', 'Franklin', 'Allegany', 'Richmond', 'Erie', 'Kings',
       'Onondaga', 'Rockland', 'Tompkins', 'Nassau', 'Albany', 'Suffolk',
       'Dutchess', 'Columbia', 'Rensselaer', 'New York', 'Saratoga',
       'Ulster', 'Oneida', 'Cattaraugus', 'Otsego', 'Queens',
       'Westchester', 'Steuben', 'Ontario', 'Warren', 'Herkimer', 'Lewis',
       'Cortland', 'Essex', 'Madison', 'Chemung', 'Schenectady', 'Fulton',
       'Schuyler', 'Orange', 'Livingston', 'Chautauqua', 'Bronx',
       'Cayuga', 'Oswego', 'Clinton', 'St. Lawrence', 'Jefferson',
       'Orleans', 'Tioga', 'Broome', 'Greene', 'Montgomery', 'Wayne',
       'Sullivan', 'Yates', 'Seneca', 'Washington', 'Niagara', 'Delaware',
       'Putnam', 'Genesee', 'Hamilton', 'Wyoming', 'Schoharie',
       'Chenango', 'Campbell'], dtype=object)

In [29]:
Charger_df.City.unique()

array(['Penfield', 'Webster', 'Saranac Lake', 'Houghton', 'Midland Beach',
       'Cheektowaga', 'Sunset Park', 'Liverpool', 'Nanuet', 'Ithaca',
       'New Hyde Park', 'Albany', 'Water Mill', 'Wappingers Falls',
       'Brooklyn', 'Hudson', 'Buffalo', 'Montebello', 'Troy', 'New York',
       'Baldwinsville', 'Rochester', 'Montauk', 'Bellmore', 'Latham',
       'Riverhead', 'Ballston Spa', 'Saugerties', 'Rome', 'Rensselaer',
       'Delmar', 'Saratoga Springs', 'Ellicottville', 'Grand Island',
       'Clifton Park', 'Mt Sinai', 'Cooperstown', 'New Paltz', 'Bayport',
       'Kew Gardens', 'Menands', 'Staten Island', 'Elmsford', 'Corning',
       'East Norwich', 'Halfmoon', 'Victor', 'Rye Brook', 'Manhattan',
       'New Hartford', 'Chestertown', 'Paul Smiths', 'Irondequoit',
       'Pleasant Valley', 'Clarkstown', 'Little Falls',
       'Rockville Centre', 'Turin', 'Shirley', 'Fairport',
       'Honeoye Falls', 'Homer', 'Olean', 'Williamsville', 'North Creek',
       'Lake Placid', 'Fre

In [34]:
# let's look for only New York City
Charger_NYC_df=Charger_df.loc[(Charger_df['County'] == 'Kings') | (Charger_df['County'] == 'Queens') | (Charger_df['County'] == 'New York') |
                                 (Charger_df['County'] == 'Bronx') | (Charger_df['County'] == 'Richmond')]
Charger_NYC_df

ID                                       Station Name  \
4     182295                           NYC FLEET DPRMBLOT8_1_L3   
6     220960                                      BRT STATION 1   
14    195668                                   1235 Linden Blvd   
19    225676                                92746 CHARGEPOINT 1   
40    201870                Central Parking - 109 E 58th Street   
...      ...                                                ...   
3062  115190    Chelnik Parking NYC 880 5th - Tesla Destination   
3066  115091  Quik Park 311 West Broadway LLC - Tesla Destin...   
3067  115047   Rapidpark 204 W 101st Street - Tesla Destination   
3077   49938                                   Nissan of Queens   
3080  168146                              HAMPTON INN STATION 1   

               City State    ZIP    County  latitude_station  \
4     Midland Beach    NY  10305  Richmond           40.5973   
6       Sunset Park    NY  11220     Kings           40.6412   
14         Brooklyn    NY  11212     Kings           40.6625   
19         New York    NY  10065  New York           40.7651   
40         New York    NY  10022  New York           40.7571   
...             ...   ...    ...       ...               ...   
3062       New York    NY  10021  New York           40.7685   
3066       New York    NY  10013  New York           40.7185   
3067       New York    NY  10025  New York           40.7975   
3077     Ozone Park    NY  11417    Queens           40.6769   
3080  Staten Island    NY  10314  Richmond           40.6039   

      longitude_station  
4              -74.0768  
6              -74.0133  
14             -73.9145  
19             -73.9638  
40             -73.9657  
...                 ...  
3062           -73.9588  
3066           -74.0025  
3067           -73.9683  
3077           -73.8448  
3080           -74.1472  

[603 rows x 8 columns]

In [35]:
# Saving  clean NY city data to CSV
Charger_NYC_df.to_csv('Resources/Demographic_Database_NYCity_EV_Stations.csv')

In [37]:
#lat long for only NYC
locations2 = Charger_NYC_df[['latitude_station', 'longitude_station']]
locationlist2 = locations.values.tolist()
locationlist2= [[float(lat),float(lon)] for [lat,lon] in locationlist]

In [38]:
#let's change the look of the point icon
import folium
import pgeocode
from folium.plugins import MarkerCluster
map3 = folium.Map(location=[40.71427, -74.00597], tiles='Stamen Terrain', zoom_start=11)

marker_cluster = MarkerCluster().add_to(map3)

for point in range(0, len(locationlist2)):
    try:
        folium.Marker(locationlist2[point], popup=Charger_NYC_df['Station Name'][point], icon=folium.Icon(color='green', icon_color='white', icon='bolt', angle=0, prefix='fa')).add_to(marker_cluster)
    except KeyError:
        print('Can not find "something"')
map3

Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"
Can not find "something"


In [39]:
map3.save('New_York_City_EV_station map.html')